<a href="https://colab.research.google.com/github/deepshadow25/colab_class_activity/blob/main/%EC%9E%90%EC%97%B0%EC%96%B4%EC%B2%98%EB%A6%AC_%ED%94%84%EB%A1%9C%EC%A0%9D%ED%8A%B8_2%EC%A1%B0_%EC%9D%B4%EC%84%B1%EC%97%B0.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 개요

사극 대본을 만들어주는 모델 구현

## 2조
* 멤버 : 이성연, 이연교, 이현중, 양성주
* 조장 : 이성연
* 발표자 : 이현중


## 진행 순서

1. 데이터 수집


2. 전처리

3. 모델링 
4. 결과 분석 및 정리
*

5. ppt 작성, 발표 스크립트 작성 후 발표

## 타임테이블




## 사용한 딥러닝 모델
* GPT3-small(based on GPT2)

## 발표자료

사용한 글꼴 : 

## 참고문헌
*

# 전처리 (정제)

조선시대 or 그 이전 옛날 어투 위주로

## 기본 전처리

In [ ]:
import re
import os
from tqdm import tqdm

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
with open('/content/drive/MyDrive/Colab Notebooks/프로젝트/자연어 팀프로젝트 자료/사극대본모음/1672043538_장녹수_-_정하연.txt','rt', encoding='cp949') as f:
    first_text=f.readlines()

In [ ]:
print(first_text)

['정하연의 장녹수 \n', '\n', '1화\n', '\n', ' \n', '#1. 장 생원의 집 행랑채 마당(밤)\n', '\n', '대문을 차고 들어오는 마님. 하인들이\n', '관솔불을 밝히고 앞뒤로 둘러쌌다.\n', '하인 하나가 노비의 방문을 벌컥 연다.\n', '마침 정사하던 노비 한 쌍이 놀라서 후닥닥\n', '떨어진다.\n', '다른 방문을 계속 열어 젖히는 하인들.\n', '여기저기서 남녀 노비의 비명 소리가\n', '들린다. 그중 한 방은 비어 있다.\n', '\n', '하인: .....\n', '\n', '험악한 얼굴\n', '\n', '\n', '\n', '마님: 뭐들 하느냐, 그 계집을 얼른\n', '끌어내지 않구.\n', '하인: (달려와) 마님, 도망을 쳤나\n', '봅니다.\n', '마님: 그 몸으로 멀리 숨지 못했을\n', '것이다. 집 안팎을 샅샅이\n', '뒤져라.\n', '\n', '흩어지는 하인들. 광이나 헛간이나 샅샅이\n', '뒤진다. 살기 등등한 기세들이다. 하인들을\n', '지시하는 마님. 장 생원이 놀라서\n', '달려온다.\n', '\n', '장생원: 부인, 무슨 일이오?\n', '마님: 영감이 상관할 일이 아닙니다.\n', '\n', '\n', '\n', '하인이 달려온다.\n', '\n', '하인: 집안에 없는 듯합니다.\n', '마님: 아랫것들 모두 끌어내라.\n', '필경 그년을 도와 숨겨 준 연놈이\n', '있을 게야.\n', '하인: 예.\n', '\n', '달려간다.\n', '이 방 저 방에서 노비 권속을 모두\n', '끌어내는 하인과 장정들.\n', '울부짖는 아이들, 미처 옷을 입지 못한\n', '아낙들 아수라장이다.\n', '\n', '마님: 바른 대로 대야 한다. 꽃봉이년을\n', '어디다 숨겼는지 이실직고하렷다.\n', '아니면 떼죽음을 면치 못할\n', '것이다.\n', '\n', '하인과 장정들, 노비 권속들을 두들겨 패기\n', '시작한다.\n', '\n', '마님: 그년을 찾아내기 

In [ ]:
find_target=['#','＃']
for text in first_text:
    for i in text:
        if i == '#':
            find_idx=0
            break
        elif i == '＃':
            find_idx=1
            break
        else:
            pass

In [ ]:
find_idx

0

In [ ]:
scene_count=0
for idx,text in enumerate(first_text):
        if text.find('#') != -1:
            scene_count+=1
        if scene_count >= 1:
            scene_start_idx=idx # 첫 씬이 시작되는 지점을 찾음
            break

In [ ]:
scene_count=0
for idx,text in enumerate(first_text):
    try:
        if text.find('＃') != -1:
            scene_count+=1
        if scene_count >= 1:
            scene_start_idx=idx # 첫 씬이 시작되는 지점을 찾음
            break
    except:
        if text.find('#') != -1:
            scene_count+=1
        if scene_count >= 1:
            scene_start_idx=idx # 첫 씬이 시작되는 지점을 찾음
            break

In [ ]:
second_text=[]
count=0
for text in first_text[scene_start_idx:]: # 제작자, 드라마 제목 등 대본의 기초정보 삭제를 위해 첫 씬이 시작되는 지점부터 시작
    text=re.sub('[a-zA-Z]','',text) # 영어오타 삭제
    text=text.rstrip() # 추후 나레이션과 구분하기위해 strip()이 아닌 rstrip()
    if text != "" and text[0] != "#": # 빈 줄 제거 및 #scene 제거
        if len(text) < 2: # 추후 나레이션 구분을 위한 처리를 위해 추가, 나레이션은 \t\t로 시작, index 1이 \t로 구분하여 나레이션 제거 예정
            text +='\t'
        second_text.append(text)
        print(count, text)
        count+=1

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
44620 성희안: 서두르지 마세요. 아직 때가 아닙니다. 술이나 드시지요.
44621 술 권한다. 화나서 벌컥 드리키는 박원종
44622 해설 : 박원종과 성희안, 두사람의 성격은 대조적이었다. 패기만만한 박원종은 성격이 급했고 성희안은 만사에 침착하고 지혜로웠다. 그런 상반된 두사람의 성격이 어울려 반정을 향해 나아가고 있었다.
44623 가마가 온다.
44624 내리는 부인.
44625 안으로 안내하는 천수.
44626 들어오는 부인.
44627 산월네: 잠깐 기다리시지요.
44628 안방에서 웃음소리
44629 부인: ...
44630 웃고있는 녹수.
44631 대감댁 마님들이 녹수의 비위를 맞추려고
44632 웃고 있다.
44633 녹수: 주상께서는 마치 세살난
44634 어린아이와 같으십니다. 가까이서
44635 뵈면 천진하기가 그지
44636 없으시지요. 나는 주상을
44637 두려워하는 사람을 모르겠어요...
44638 세상에 착하고 순한 양반이 우리
44639 주상전하신데 말씀입니다. 그런데
44640 왜들 그렇게 무서워 하시는
44641 겁니까.
44642 웃는 녹수.
44643 산월: (밖에서) 마마, 정동마님께서
44644 오셨습니다.
44645 녹수: 기다리시라고 하게. 지금은
44646 방안에 손님이 가득하니...
44647 산월네 미안해서 부인 본다.
44648 산월네: 잠시 건너방에 드셔계시겠습니까.
44649 부인: 아닐세, 여기서 기다리겠네.
44650 안에서 다시 웃음소리
44651 부인: ...
44652 수치심에 외면한다.
44653 밖에서 천수가 다른 부인을 안내해 온다.
44654 천수: 이쪽으로 드시지요...
44655 마주치는 부인들.
44656 챙피해서 얼른 외면하는 부인들.
44657 원진: 귀가 먹었냐. 일부러 줄을
44658 세운다고 안하냐.
44659 산월: 일부러 줄을 세우다니요.
44660 원진: 내노라하는 대감집 마님들께서
44661 녹수

In [ ]:
second_text[0]

'대문을 차고 들어오는 마님. 하인들이'

In [ ]:
second_text[-3][:2]

'해설'

In [ ]:
third_text=[]
count=0
for text in second_text:
    if text[:2] != "해설": # \t\t로 시작하는 나레이션 제외
    # 작가가 어떨때는 \t를 한번넣냐 두번넣냐로 나레이션인지 대사의 줄바꿈인지를 구분하고 어떨때는 \s를 다르게 넣는 방식으로 구분해놔서 완벽하게 구분하기 어려움
        text=re.sub('\s+',' ',text).strip() # 다수개의 공백 제거 및 양옆 공백 제거, 띄워쓰기로 하면 문법이 맞는 경우도 있고 틀린 경우도 있음
        third_text.append(text)
        print(count, text)
        count+=1

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
44238 박종원: 이장곤이 아직 살아 있습니까.
44239 유자광: 모르고 계시는군요. 주상께 몸을 더럽힌 부인을 베고 귀양 길에 오른 이장곤이 금무도사를 죽이고 산으로 들어갔다는 소문입니다.
44240 박종원: 산으로 들어가 도적이 됐단 말씀입니까.
44241 유자광: 도적은 도적이되 보통 도적이 아니구요, 그를 따르는 무리가 적지 않다고 합니다.
44242 박종원: ...
44243 유자광: 항간에는 이장곤의 무리가 도성까지 쳐들어올거라는 소문이 파다합니다.
44244 박종원: 그렇게 세력이 큽니까.
44245 유자광: 이장곤의 무리가 아무리 크다고 한들 도성까지야 넘보겠습니까. 허나 민심이 문제지요. 민심이 떠나고 있으니 그게 문젭니다.
44246 박종원: ...
44247 유자광: (웃으며) 박공, 아무리 이 나라가 썩었기로서니 이장곤 같은 무리베에게 나라를 넘겨줘서야 되겠습니까. (웃고는) 허나 때를 잃으면 다시는 오지 않는 법입니다. (일어나며) 나는 그만 가보겠오이다.
44248 나가는 유자광
44249 박원종: ...
44250 입 꽉 다물고 있는 박원종
44251 유자광이 간다.
44252 오는 유자광. 헛기침하더니
44253 유자광: (우렁차게) 이리 오너라.
44254 제안: ...(덩그렁)
44255 유자광: 보잘것 없는 종수의 일원이기는 하나 이나라 종묘사직을 염려 하는데 있어서는 결코 뒤짐이 없다고 자부하고 있사옵니다. 대군, 주상전하께옵서 그나마 어려워하는 왕언의 어른이 계시다면 대군뿐이 아니옵니까. 이런 터에 가만히 앉아서 구경만 하시는 것은 옳은 일이 아니옵니다.
44256 제안: 그래서요.
44257 유자광: 대군께서 나셔야 합니다.
44258 제안: ...
44259 유자광: 대군께서 실성한 사람도 흉내를 내서 천하를 떠돈다는 소식을 듣고 제 마음이 찢어지도록 아펐습니다. 주상을 바로잡을 분이 오직 한분 뿐이신데 그분께서 광인의 흉내를 내고 계시니 정작 실성한 

In [ ]:
fourth_text=[]
for text in third_text:

    if text.find('(') != -1: # 감정묘사에 쓰이는 '(감정묘사)' 제거
        one_text=text[:text.find('(')].strip()
        two_text=text[text.find(')')+1:].strip()
        text=one_text + two_text

    start_idx=text.find(':')+1 # 말하는 인물을 나타내는 ':' 이후로 가져올 수 있도록 하기위함
    if start_idx - 1 != -1:
        text=(text[start_idx:]).strip() # ':' 이후로 문자를 가져오고 양옆의 공백 제거

        if re.sub('[^가-힣]','',text) != '': # "...!!..." 같은 한글 없이 감정을 나타내고자 했던 특수기호를 제외하고 삭제
            fourth_text.append(text)
    else:
        try:
            fourth_text[-1]+=' ' + text.strip() # 대사 줄바꿈을 합쳐주기
        except:
            pass

fourth_text[-1]=fourth_text[-1][:fourth_text[-1].find('엔딩')] # '엔딩' 제거

In [ ]:
fourth_text[-1] = fourth_text[-1][:40]
fourth_text

['뭐들 하느냐, 그 계집을 얼른 끌어내지 않구.',
 '마님, 도망을 쳤나 봅니다.',
 '그 몸으로 멀리 숨지 못했을 것이다. 집 안팎을 샅샅이 뒤져라. 흩어지는 하인들. 광이나 헛간이나 샅샅이 뒤진다. 살기 등등한 기세들이다. 하인들을 지시하는 마님. 장 생원이 놀라서 달려온다.',
 '부인, 무슨 일이오?',
 '영감이 상관할 일이 아닙니다. 하인이 달려온다.',
 '집안에 없는 듯합니다.',
 '아랫것들 모두 끌어내라. 필경 그년을 도와 숨겨 준 연놈이 있을 게야.',
 '예. 달려간다. 이 방 저 방에서 노비 권속을 모두 끌어내는 하인과 장정들. 울부짖는 아이들, 미처 옷을 입지 못한 아낙들 아수라장이다.',
 '바른 대로 대야 한다. 꽃봉이년을 어디다 숨겼는지 이실직고하렷다. 아니면 떼죽음을 면치 못할 것이다. 하인과 장정들, 노비 권속들을 두들겨 패기 시작한다.',
 '그년을 찾아내기 전에는 누구 하나 살아남지 못할 것이다. 더욱 거칠어지는 매질. 비명 소리.',
 '부인, 내 실수요, 내 체면을 봐서라도...',
 '오입질하는 체면은 따로 있답디까. 영감이 누구 덕이 이만큼 사는데 나 모르게 천한 종년을 건드려요. 거기다 배까지 불렀으니 내 이 년을 찾아내서 발기발기 찢어 죽이기 전에는 숨을 쉬고 살 수가 없어요. 뭐하고 있느냐. 아직도 그년의 행방을 찾지 못했느냐? 하인이 개똥이네를 끌고 온다. 납작 엎드려 벌벌 떠는 개똥네.',
 '어디다 숨겼느냐?',
 '마, 마님.',
 '어서 대지 못해?',
 '초저녁에 진통이 시작돼서 산월 아범이 업고 나가는 것을 보았습니다요.',
 '뭐, 뭣이라구? 진통이라니... 그년이 해산을 한단 말이냐.',
 '마, 만삭이 돼서... 마님이 개똥을 바라보자 개똥은 외면한다. 더이상 참지 못하겠다는 듯이 눈이 뒤집히는 마님. 짐승 같은 소리를 내지르더니 옆에 선 장정의 손에서 몽둥이를 빼앗아 들더니 개똥네의 머리를 사정없이 내리친다. 푹 고꾸라지는 개똥네. 계속 내리치는 마님. 미친 사람 같다. 관솔불 들고 이

## 함수화

In [ ]:
# 함수화

def antique_term(path, encoding):
    with open(path,'r', encoding=encoding) as f:
        first_text=f.readlines()

    find_target=['#','＃'] # '#'과 '＃' 이렇게 두가지가 쓰임
    for text in first_text:
        for i in text:
            if i == '#':
                find_idx=0
            elif i == '＃':
                find_idx=1
            else:
                pass

    scene_count=0
    for idx,text in enumerate(first_text):
        if text.find(find_target[find_idx]) != -1:
            scene_count+=1
        if scene_count >= 1:
            scene_start_idx=idx # 첫 씬이 시작되는 지점을 찾음
            break

    second_text=[]
    for text in first_text[scene_start_idx:]: # 제작자, 드라마 제목 등 대본의 기초정보 삭제를 위해 첫 씬이 시작되는 지점부터 시작
        text=re.sub('[a-zA-Z]','',text) # 영어오타 삭제
        text=text.rstrip() # 추후 나레이션과 구분하기위해 strip()이 아닌 rstrip()
        if text != "" and text[0] != find_target[find_idx]: # 빈 줄 제거 및 #scene 제거
            if len(text) < 2: # 추후 나레이션 구분을 위한 처리를 위해 추가, 나레이션은 \t\t로 시작, index 1이 \t로 구분하여 나레이션 제거 예정
                text +='\t'
            second_text.append(text)

    third_text=[]
    for text in second_text:
        if text[1] != "해설": # \t\t로 시작하는 나레이션 제외
        # 작가가 어떨때는 \t를 한번넣냐 두번넣냐로 나레이션인지 대사의 줄바꿈인지를 구분하고 어떨때는 \s를 다르게 넣는 방식으로 구분해놔서 완벽하게 구분하기 어려움
            text=re.sub('\s+',' ',text).strip() # 다수개의 공백 제거 및 양옆 공백 제거, 띄워쓰기로 하면 문법이 맞는 경우도 있고 틀린 경우도 있음
            third_text.append(text)

    fourth_text=[]
    for text in third_text:

        # if text.find('(') != -1: # 감정묘사에 쓰이는 '(감정묘사)' 제거
        #     one_text=text[:text.find('(')].strip()
        #     two_text=text[text.find(')')+1:].strip()
        #     text=one_text + two_text

        start_idx=text.find(':') # 말하는 인물을 나타내는 ':' 이후로 가져올 수 있도록 하기위함
        if start_idx != -1:
            text=text[start_idx+1:].strip() # ':' 이후로 문자를 가져오고 양옆의 공백 제거

            if re.sub('[^가-힣]','',text) != '': # "...!!..." 같은 한글 없이 감정을 나타내고자 했던 특수기호를 제외하고 삭제
                fourth_text.append(text)
        else:
            try:
                fourth_text[-1]+=' ' + text.strip() # 대사 줄바꿈을 합쳐주기
            except:
                pass

    try:
        fourth_text[-1]=fourth_text[-1][:fourth_text[-1].find('엔딩')] # '엔딩' 제거
    except:
        pass
        
    return fourth_text

In [ ]:
root_path='/content/drive/MyDrive/Colab Notebooks/프로젝트/자연어 팀프로젝트 자료/사극대본모음/'

In [ ]:
os.listdir(root_path)[0]

'1672043593_명성황후.txt'

In [ ]:
text=[]
for text_file in tqdm(os.listdir(root_path)):
    try:
        text.append(antique_term(root_path + text_file, 'utf-8'))
    except:
        text.append(antique_term(root_path + text_file, 'cp949'))

 33%|███▎      | 2/6 [00:01<00:02,  1.53it/s]


IsADirectoryError: ignored

In [ ]:
text[0]

['겨울을 가르고 피어나는 것이 벚꽃이라고 한다지? 나직히 중얼거리듯 내뱉는 명성 분바르듯 손을 황급히 거두고 명성황후를 바라보는 홍상궁',
 '그렇게 활짝 피었다가 마치 바람에 날리는 함박눈처럼 하루 아침에 저버리는 것이 또한 벚꽃 이렷다 재밌다는 듯 싱긋 웃는 명성 그저 조심스럽게 바라만 보는 홍상궁',
 '내 말이 틀렸느냐',
 '무슨 말씀이신지',
 '왜인들의 생사관이 그렇다는 것이야. 죽고 사는 것에 연연하지 않는 것이 왜인들의 특색이 다......? 기가 막히다는 듯 소리 없이 웃는 명성 고종이 앉은 뒤쪽에 장지문이 열렸고 그 문으로 오후의 눈부신 햇살이 방안으로 쏟아져 들어오고 있다 고종의 의자 옆 뒤쪽에 발이 짙게 내려져 있다 눈부셔하며 발 뒤에 앉은 여인의 자태를 잡으려는 듯 애쓰는 미우라의 눈빛 그러나 형체가 드러났다가 이내 햇살 속으로 사라지는 그림자',
 '(웃으며) 죽고 사는 것에 연연하지 않는다?',
 '그렇습니다 전하 꼿꼿이 서서 고개를 숙이는 미우라 공사',
 '일본이 청국과 같은 대국을 상대로 승전할 수 있었던 비결이 거기에 있었습니다',
 '비굴하게 살아 남느니 명예롭게 죽는 것이 일본무사의 정신입니다. 전하, 전하께옵서 일본 을 방문할 기회가 계시다면 우에노 공원에 활짝 핀 벚꽃 구경을 하시게 될 것입니다. 장관이지요. 그 눈부신 자태에 전하께옵서는 탄성을 발하실 것이나 하오나 그 보다 더 황홀하고 아름다운 것은 벚꽃이 지는 모습입니다. 눈이 내리듯 바람에 날리며 지는 꽃잎을 보고 있노라면 저도 모르게 두 주먹이 불끈 쥐어집니다. 요시, 나도 저렇게 살리라. 국가와 대의를 위해서 벚꽃처럼 살다 가리라....',
 '(미소) 미우라 공사는 군인이 아니라 시인입니다 그려 (웃으며) 아름다운 꽃잎이 덧없이 지는 모습을 보고 있노라면 눈물이 절러 나는 것이 인지상정이 아닙니까',
 '(단호히) 그것은 패배자의 시각이지요',
 '일본인은 죽음을 통해서 다시 태어난다는 것을 전하께옵서는 명심하셔야 할 것이옵니다 위협적인 미우라의 눈빛 순

In [ ]:
type(text)

list

In [ ]:
text_msempress = antique_term('/content/drive/MyDrive/Colab Notebooks/프로젝트/자연어 팀프로젝트 자료/사극대본모음/1672043593_명성황후.txt', 'cp949')

In [ ]:
text_msempress[-3] #= text_msempress[-1][:2]

'오늘은 내 나라가 힘이 없고 약해서 네 놈들에게 이런 수모를 당한다만 언젠가는 반드시 부국강병을 이뤄서 오늘 진 빚을 갚아줄 것이다. 내가 너희들의 만행을 다 내 눈 속에서 담아서 갈 것이니 내 백성이 어찌 오늘의 일을 잊겠느냐'

In [ ]:
max(text_msempress, key=len)

'(물색없이 웃으며) 따라야지요. 며느님을 손수 고르시겠다는데 대원군 으흠 대비 어서 말씀을 하세요 대원군 그러면 흥인군 셋은 골라야지요. 명색이 삼간택인데 달랑 한 사람만 들어오라고 하는 것은 대원군 저더러 며느리를 고르라 하시니 그러면 제가 정하겠습니다 좀 계면쩍어 차를 한모금 마시는데 대원군 나는 민치록의 여식으로 정했습니다 찻잔을 떨어뜨릴 뻔한다 대원군 민치록의 여식이 편모슬하라고 하니 외척이 발호할 염려는 하지 않아도 될 것이 아닙니까 천연덕스럽게 웃는 대원군 <명성황후 3회 끝> 제 4회 씬 희정당의 안방 천연덕스럽게 웃고 있는 대원군 거의 찻잔을 떨어뜨릴 뻔했던 조대비 겨우 몸을 추스리고 잔기침을 해댄다 민망해서 조대비를 바라보는 왕대비와 대비 흥인군 민치록의 여식을 중전으로 낙점을 하셨다 그 말씀이지요? 내 눈에도 민치록의 여식이 쏙 들어옵디다. 군계일학이란 이럴 때를 두고 하는 말이 아니겠습니까 (껄껄 웃으며) 주상께서 친정을 하시게 된 마당에 중전까지 맞으시게 됐으니 경사가 겹쳤습니다그려 (웃어대는데) 왕대비 (조대비의 눈치를 보며) 민치록의 여식이라니오. 저는 조면호의 여식으로 들었습니다 흥인군 (버럭 내지르듯) 조면호의 여식이라니오. 방금 내 아우님께서 민치록의 여식으로 정한다고 하질 않았습니까 대원군 (막듯이) 딱히 그렇다는 것이 아니고 마마께서 저더러 정하라 하시니 저라면 민치록의 여식이 마음에 든다고 말씀을 드린 것뿐입니다 대비 (물색없이) 참하기는 민치록의 여식이 돋보였습니다 (끄덕인다) 대원군 (조대비에게) 마마. 달리 의중에 두신 규수가 계시면 말씀을 하시지요 조대비 으흠 대원군 ......(웃으며 보고 있다) 왕대비 민치록의 여식이 부대부인과는 항렬이 어찌되는지 대원군 무슨 말씀이신지 왕대비 (힘내서 나서며) 민치록의 양자로 들어간 민승호가 부대부인과는 남매지간이라고 들었기에 흥인군 (버럭) 촌수로 따지면 십이 촌지간인데 그것도 인척이라고 할 수가 있겠습니까. 그렇게 치면 이웃 사촌이 더 가깝지요. 왕대비께서는 별 트집을 다 

In [ ]:
len()+text_msemperss+max()

TypeError: ignored

## 함수화(등장인물별)

In [ ]:
# 함수화

def antique_term_char(path, encoding):
    with open(path,'r', encoding=encoding) as f:
        first_text=f.readlines()

    char_dict={}

    find_target=['#','＃'] # '#'과 '＃' 이렇게 두가지가 쓰임
    for text in first_text:
        for i in text:
            if i == '#':
                find_idx=0
            elif i == '＃':
                find_idx=1
            else:
                pass

    scene_count=0
    for idx,text in enumerate(first_text):
        if text.find(find_target[find_idx]) != -1:
            scene_count+=1
        if scene_count >= 1:
            scene_start_idx=idx # 첫 씬이 시작되는 지점을 찾음
            break

    second_text=[]
    for text in first_text[scene_start_idx:]: # 제작자, 드라마 제목 등 대본의 기초정보 삭제를 위해 첫 씬이 시작되는 지점부터 시작
        text=re.sub('[a-zA-Z]','',text) # 영어오타 삭제
        text=text.rstrip() # 추후 나레이션과 구분하기위해 strip()이 아닌 rstrip()
        if text != "" and text[0] != find_target[find_idx]: # 빈 줄 제거 및 #scene 제거
            if len(text) < 2: # 추후 나레이션 구분을 위한 처리를 위해 추가, 나레이션은 \t\t로 시작, index 1이 \t로 구분하여 나레이션 제거 예정
                text +='\t'
            second_text.append(text)

    third_text=[]
    for text in second_text:
        if text[1] != "해설": # \t\t로 시작하는 나레이션 제외
        # 작가가 어떨때는 \t를 한번넣냐 두번넣냐로 나레이션인지 대사의 줄바꿈인지를 구분하고 어떨때는 \s를 다르게 넣는 방식으로 구분해놔서 완벽하게 구분하기 어려움
            text=re.sub('\s+',' ',text).strip() # 다수개의 공백 제거 및 양옆 공백 제거, 띄워쓰기로 하면 문법이 맞는 경우도 있고 틀린 경우도 있음
            third_text.append(text)

    for text in third_text:

        start_idx=text.find(':') # 말하는 인물을 나타내는 ':' 이후로 가져올 수 있도록 하기위함

        if start_idx != -1:
            char_key=text[:start_idx].strip()
            char_text=text[start_idx+1:].strip()
            if char_key not in char_dict: # 캐릭터별 대사 분류
                char_dict[char_key]=[]

            if re.sub('[^가-힣]','',char_text) != '': # "...!!..." 같은 한글 없이 감정을 나타내고자 했던 특수기호를 제외하고 삭제
                char_dict[char_key].append(char_text)

        else:
            try:
                char_dict[char_key][-1]+=' ' + char_text.strip() # 대사 줄바꿈을 합쳐주기
            except:
                pass

    return char_dict

In [ ]:
antique_term_char('/content/drive/MyDrive/Colab Notebooks/프로젝트/자연어 팀프로젝트 자료/사극대본모음/1672043593_명성황후.txt','cp949')

{'명성황후': [],
 '명성': ['겨울을 가르고 피어나는 것이 벚꽃이라고 한다지? 겨울을 가르고 피어나는 것이 벚꽃이라고 한다지? 겨울을 가르고 피어나는 것이 벚꽃이라고 한다지?',
  '그렇게 활짝 피었다가 마치 바람에 날리는 함박눈처럼 하루 아침에 저버리는 것이 또한 벚꽃 그렇게 활짝 피었다가 마치 바람에 날리는 함박눈처럼 하루 아침에 저버리는 것이 또한 벚꽃 그렇게 활짝 피었다가 마치 바람에 날리는 함박눈처럼 하루 아침에 저버리는 것이 또한 벚꽃 그렇게 활짝 피었다가 마치 바람에 날리는 함박눈처럼 하루 아침에 저버리는 것이 또한 벚꽃',
  '내 말이 틀렸느냐',
  '왜인들의 생사관이 그렇다는 것이야. 죽고 사는 것에 연연하지 않는 것이 왜인들의 특색이 왜인들의 생사관이 그렇다는 것이야. 죽고 사는 것에 연연하지 않는 것이 왜인들의 특색이 왜인들의 생사관이 그렇다는 것이야. 죽고 사는 것에 연연하지 않는 것이 왜인들의 특색이 왜인들의 생사관이 그렇다는 것이야. 죽고 사는 것에 연연하지 않는 것이 왜인들의 특색이 왜인들의 생사관이 그렇다는 것이야. 죽고 사는 것에 연연하지 않는 것이 왜인들의 특색이 왜인들의 생사관이 그렇다는 것이야. 죽고 사는 것에 연연하지 않는 것이 왜인들의 특색이',
  '(발 뒤에서) 천하고 귀하고 간에 다 소중한 것이 인명입니다 (발 뒤에서) 천하고 귀하고 간에 다 소중한 것이 인명입니다 (발 뒤에서) 천하고 귀하고 간에 다 소중한 것이 인명입니다 (발 뒤에서) 천하고 귀하고 간에 다 소중한 것이 인명입니다',
  '전하께옵서 일본의 벚꽃구경을 가실 일은 없을 것입니다 ...... ...... ...... ......',
  '(마치 탄식하듯) 살고 죽는 것에 연연하지 않는다.....',
  '자네가 올해로 쉬흔을 넘겼다고 했든가',
  '(힐끔 본다) (힐끔 본다)',
  '(재밌다는 듯) 농을 하자?',
  '자네와 내가 서른 해가 넘도록 함께 지냈으니 그만 농두 주고 받지 못할 처지겠는가',
  '(생각에 잠기며)...

# Modeling

In [ ]:
pip install transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 5.8 MB 1.9 MB/s 
     |████████████████████████████████| 7.6 MB 72.1 MB/s 
     |████████████████████████████████| 182 kB 92.8 MB/s 


## GPT3
failed

In [ ]:
# gpt3-kor-small_based_on_gpt2
from transformers import BertTokenizerFast, GPT2LMHeadModel
from transformers import AutoConfig

tokenizer_gpt3 = BertTokenizerFast.from_pretrained(
    "kykim/gpt3-kor-small_based_on_gpt2", bos_token='[/s]', eos_token='[/s]', 
    unk_token='[UNK]', pad_token='[PAD]', mask_token='[MASK]')
input_ids = tokenizer_gpt3.encode("text to tokenize")[1:]  # remove cls token

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'GPT2Tokenizer'. 
The class this function is called from is 'BertTokenizer'.
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'GPT2Tokenizer'. 
The class this function is called from is 'BertTokenizerFast'.
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
input_ids

[34725, 8385, 8086, 17528, 17528, 8274, 14470, 27108, 3]

In [ ]:
model_gpt3 = GPT2LMHeadModel.from_pretrained("kykim/gpt3-kor-small_based_on_gpt2")
config = AutoConfig.from_pretrained('kykim/gpt3-kor-small_based_on_gpt2')


In [ ]:
config.update_from_string("vocab_size=52002")

In [ ]:
print(tokenizer_gpt3.bos_token_id)
print(tokenizer_gpt3.eos_token_id)
print(tokenizer_gpt3.pad_token_id)
print('-' * 10)
print(tokenizer_gpt3.decode(1))
print(tokenizer_gpt3.decode(2))
print(tokenizer_gpt3.decode(3))
print(tokenizer_gpt3.decode(4))

42000
42000
0
----------
[UNK]
[CLS]
[SEP]
[MASK]


In [ ]:
tokenizer_gpt3

PreTrainedTokenizerFast(name_or_path='kykim/gpt3-kor-small_based_on_gpt2', vocab_size=42000, model_max_len=2048, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'bos_token': '[/s]', 'eos_token': '[/s]', 'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'})

In [ ]:
type(tokenizer_gpt3)

transformers.models.bert.tokenization_bert_fast.BertTokenizerFast

In [ ]:
tokenizer_gpt3.all_special_tokens

['[/s]', '[UNK]', '[SEP]', '[PAD]', '[CLS]', '[MASK]']

In [ ]:
import pandas as pd
import tqdm
import urllib.request

In [ ]:
train_data = fourth_text
len(train_data)

15604

In [ ]:
def get_chat_data_gpt3():
  for t in train_data:
    bos_token = [tokenizer_gpt3.bos_token_id]
    eos_token = [tokenizer_gpt3.eos_token_id]
    sent = tokenizer_gpt3.encode(t) 
    yield bos_token + sent + eos_token
     

In [ ]:
import tensorflow as tf

In [ ]:
batch_size = 8

In [ ]:
dataset = tf.data.Dataset.from_generator(get_chat_data_gpt3, output_types=tf.int32)

In [ ]:
dataset = dataset.padded_batch(batch_size=batch_size, padded_shapes=(None,), padding_values=tokenizer_gpt3.pad_token_id)

In [ ]:
dataset

<PaddedBatchDataset element_spec=TensorSpec(shape=(None, None), dtype=tf.int32, name=None)>

In [ ]:
for batch in dataset:
    print(batch)
    break     

tf.Tensor(
[[42000     2  4242  8087 28030  8841  2014  2430  2247 18230 17877 17669
  25591  5510  8123  2016     3 42000     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0]
 [42000     2  4019  8403  2014 19568  8051  6654  8155 17135  2016     3
  42000     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0]
 [42000     2  2430 29168 16793  5111  8038 37119 14165  2016  6282 27301
   8051  4906  9623  8018 38189  8042  2016  7971 16882  7649 23004  2016
  32474  8155  7738 26492  8155  4906  9623  8018  3363 14870  2016 30625
  16043  8112  2469  8016 21281  2016

In [ ]:
tokenizer_gpt3.decode(batch[0])

'[/s] [CLS] 뭐들 하느냐, 그 계집을 얼른 끌어내지 않구. [SEP] [/s] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD]'

In [ ]:
tokens, token = [], []

In [ ]:
tokens = []
for i in text:
    for j in i:
        tokens.append(tokenizer_gpt3.encode(j, return_tensors='tf'))

tokens

[<tf.Tensor: shape=(1, 3), dtype=int32, numpy=array([[   2, 5921,    3]], dtype=int32)>,
 <tf.Tensor: shape=(1, 3), dtype=int32, numpy=array([[   2, 7677,    3]], dtype=int32)>,
 <tf.Tensor: shape=(1, 3), dtype=int32, numpy=array([[   2, 7677,    3]], dtype=int32)>,
 <tf.Tensor: shape=(1, 3), dtype=int32, numpy=array([[   2, 6165,    3]], dtype=int32)>,
 <tf.Tensor: shape=(1, 3), dtype=int32, numpy=array([[   2, 5230,    3]], dtype=int32)>,
 <tf.Tensor: shape=(1, 2), dtype=int32, numpy=array([[2, 3]], dtype=int32)>,
 <tf.Tensor: shape=(1, 3), dtype=int32, numpy=array([[   2, 2190,    3]], dtype=int32)>,
 <tf.Tensor: shape=(1, 3), dtype=int32, numpy=array([[   2, 5887,    3]], dtype=int32)>,
 <tf.Tensor: shape=(1, 2), dtype=int32, numpy=array([[2, 3]], dtype=int32)>,
 <tf.Tensor: shape=(1, 3), dtype=int32, numpy=array([[   2, 4345,    3]], dtype=int32)>,
 <tf.Tensor: shape=(1, 3), dtype=int32, numpy=array([[   2, 3681,    3]], dtype=int32)>,
 <tf.Tensor: shape=(1, 3), dtype=int32, numpy

In [ ]:
adam = tf.keras.optimizers.Adam(learning_rate=3e-5, epsilon=1e-08)

In [ ]:

steps = len(train_data) // batch_size + 1
print(steps)


1951


In [ ]:
import pandas as pd
from tqdm import tqdm
import urllib.request

In [ ]:
EPOCHS = 5

for epoch in range(EPOCHS):
  epoch_loss = 0

  for batch in tqdm(dataset, total=steps):
      with tf.GradientTape() as tape:
          result = model_gpt3(batch, labels=batch)
          loss = result[0]
          batch_loss = tf.reduce_mean(loss)
    #   if batch > steps:
    #       break    
      grads = tape.gradient(batch_loss, model_gpt3.trainable_variables)
      adam.apply_gradients(zip(grads, model_gpt3.trainable_variables))
      epoch_loss += batch_loss / steps

      

  print('[Epoch: {:>4}] cost = {:>.9}'.format(epoch + 1, epoch_loss))

  0%|          | 0/1951 [00:00<?, ?it/s]


AttributeError: ignored

In [ ]:
import numpy as np

In [ ]:
output = model_gpt3.generate(input_ids, max_length=50, early_stopping=True, eos_token_id=tokenizer_gpt3.eos_token_id)
output

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:42000 for open-end generation.


AttributeError: ignored

In [ ]:
decoded_sentence = tokenizer_gpt3.decode(output[0].numpy().tolist())

In [ ]:
decoded_sentence

'</s> 오늘도 좋은 하루!</s>'

In [ ]:
decoded_sentence.replace("</s>", "")

' 오늘도 좋은 하루!'

In [ ]:

def return_answer_by_chatbot(user_text):
  sent = user_text
  input_ids = [tokenizer.bos_token_id] + tokenizer.encode(sent)
  input_ids = tf.convert_to_tensor([input_ids])
  output = model.generate(input_ids, max_length=100, do_sample=True, top_k=20)
  sentence = tokenizer.decode(output[0].numpy().tolist())
  chatbot_response = sentence.replace("</s>", "").strip("<PAD>")
  return chatbot_response

## LM_tutorial

In [ ]:
!pip install transformers datasets evaluate

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 452 kB 4.2 MB/s 
     |████████████████████████████████| 81 kB 11.1 MB/s 
     |████████████████████████████████| 132 kB 68.6 MB/s 
     |████████████████████████████████| 213 kB 94.7 MB/s 
     |████████████████████████████████| 127 kB 79.1 MB/s 
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3


In [ ]:
# from datasets import load_dataset

# eli5 = load_dataset("eli5", split="train_asks[:5000]")

Downloading:   0%|          | 0.00/3.50k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/576M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/21.1M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/53.0M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/286M [00:00<?, ?B/s]

...

Downloading:   0%|          | 0.00/17.7M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/330M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/18.7M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/36.2M [00:00<?, ?B/s]

Dataset eli5 downloaded and prepared to /root/.cache/huggingface/datasets/eli5/LFQA_reddit/1.0.0/17574e5502a10f41bbd17beba83e22475b499fa62caa1384a3d093fc856fe6fa. Subsequent calls will reuse this data.


In [ ]:
# eli5 = eli5.train_test_split(test_size=0.2)

In [ ]:
# eli5["train"][0]

In [ ]:
# type(eli5)

datasets.arrow_dataset.Dataset

In [ ]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("distilgpt2")

Downloading:   0%|          | 0.00/762 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/456k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

In [ ]:
# eli5 = eli5.flatten()
# eli5["train"][0]

{'q_id': 'nyxfp',
 'title': 'Few questions about this space walk photograph.',
 'selftext': '_URL_0_\n\nThis was on the front page earlier and I have a few questions about it. Is it possible to calculate how fast the astronaut would be orbiting the earth? Also how does he stay close to the shuttle so that he can return safely, i.e is he orbiting at the same speed and can therefore stay next to it? And finally if his propulsion system failed, would he eventually re-enter the atmosphere and presumably die?',
 'document': '',
 'subreddit': 'askscience',
 'answers.a_id': ['c3d1aib', 'c3d4lya'],
 'answers.text': ["The velocity needed to remain in orbit is equal to the square root of Newton's constant times the mass of earth divided by the distance from the center of the earth. I don't know the altitude of that specific mission, but they're usually around 300 km. That means he's going 7-8 km/s.\n\nIn space there are no other forces acting on either the shuttle or the guy, so they stay in the

In [ ]:
def preprocess_function(examples):
    return tokenizer([" ".join(x) for x in examples["answers.text"]], truncation=True)

In [ ]:
train_sr = pd.Series(train_data)

In [ ]:
train_sr

0                                뭐들 하느냐, 그 계집을 얼른 끌어내지 않구.
1                                          마님, 도망을 쳤나 봅니다.
2        그 몸으로 멀리 숨지 못했을 것이다. 집 안팎을 샅샅이 뒤져라. 흩어지는 하인들. ...
3                                              부인, 무슨 일이오?
4                               영감이 상관할 일이 아닙니다. 하인이 달려온다.
                               ...                        
15599                                    왕자의 예는 갖춰주는 것이...
15600                                        그러는 것이 좋겠습니까.
15601                         나는 반댑니다. 연산을 땅속에 묻어줘서는 안됩니다.
15602                         무령군께서는 한때 선왕의 총애를 받던분이 아닙니까.
15603             더 이상 왈가왈부하지 마세요. 폐주의 일은 내가 알아서 처리 할 것입니다
Length: 15604, dtype: object

In [ ]:
tokenized_lm = train_sr.map(
    preprocess_function,
    #batched=True,
    #num_proc=4,
    #remove_columns=eli5["train"].column_names,
)

TypeError: ignored

In [ ]:
type(fourth_text)

list

In [ ]:
tokenized_fourtext = tokenizer(fourth_text)

Token indices sequence length is longer than the specified maximum sequence length for this model (1823 > 1024). Running this sequence through the model will result in indexing errors


In [ ]:
block_size = 128


def group_texts(examples):
    concatenated_examples = {k: sum(examples[k], []) for k in examples.keys()}
    total_length = len(concatenated_examples[list(examples.keys())[0]])
    total_length = (total_length // block_size) * block_size
    result = {
        k: [t[i : i + block_size] for i in range(0, total_length, block_size)]
        for k, t in concatenated_examples.items()
    }
    result["labels"] = result["input_ids"].copy()
    return result

In [ ]:
lm_dataset = tokenized_fourtext.map(group_texts, batched=True, num_proc=4)

AttributeError: ignored

In [ ]:
fourth_dic = {i : fourth_text[i] for i in range(len(fourth_text))}
#fourth_dic = {}
#for i in range(len(fourth_text)):
#    fourth_dic = {i : fourth_text[i]} 
    # print(fourth_dic)
#fourth_dic

In [ ]:
lm_dataset = group_texts(fourth_dic)

TypeError: ignored

In [ ]:
from transformers import DataCollatorForLanguageModeling

data_collator = DataCollatorForLanguageModeling(tokenizer=tokenizer, mlm=False, return_tensors="tf")

In [ ]:
# from transformers import DataCollatorForLanguageModeling

# data_collator = DataCollatorForLanguageModeling(tokenizer=tokenizer, mlm_probability=0.15, return_tensors="tf")

In [ ]:
from transformers import create_optimizer, AdamWeightDecay

optimizer = AdamWeightDecay(learning_rate=2e-5, weight_decay_rate=0.01)

In [ ]:
from transformers import TFAutoModelForCausalLM

model = TFAutoModelForCausalLM.from_pretrained("distilgpt2")

loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--distilgpt2/snapshots/ee0b29d316a6a55fd15c50c4a97aca80ab4dd66a/config.json
Model config GPT2Config {
  "_name_or_path": "distilgpt2",
  "_num_labels": 1,
  "activation_function": "gelu_new",
  "architectures": [
    "GPT2LMHeadModel"
  ],
  "attn_pdrop": 0.1,
  "bos_token_id": 50256,
  "embd_pdrop": 0.1,
  "eos_token_id": 50256,
  "id2label": {
    "0": "LABEL_0"
  },
  "initializer_range": 0.02,
  "label2id": {
    "LABEL_0": 0
  },
  "layer_norm_epsilon": 1e-05,
  "model_type": "gpt2",
  "n_ctx": 1024,
  "n_embd": 768,
  "n_head": 12,
  "n_inner": null,
  "n_layer": 6,
  "n_positions": 1024,
  "reorder_and_upcast_attn": false,
  "resid_pdrop": 0.1,
  "scale_attn_by_inverse_layer_idx": false,
  "scale_attn_weights": true,
  "summary_activation": null,
  "summary_first_dropout": 0.1,
  "summary_proj_to_labels": true,
  "summary_type": "cls_index",
  "summary_use_proj": true,
  "task_specific_params

Downloading:   0%|          | 0.00/328M [00:00<?, ?B/s]

loading weights file tf_model.h5 from cache at /root/.cache/huggingface/hub/models--distilgpt2/snapshots/ee0b29d316a6a55fd15c50c4a97aca80ab4dd66a/tf_model.h5
All model checkpoint layers were used when initializing TFGPT2LMHeadModel.

All the layers of TFGPT2LMHeadModel were initialized from the model checkpoint at distilgpt2.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFGPT2LMHeadModel for predictions without further training.


In [ ]:
tf_train_set = model.prepare_tf_dataset(
    lm_dataset["train"],
    shuffle=True,
    batch_size=16,
    collate_fn=data_collator,
)

tf_test_set = model.prepare_tf_dataset(
    lm_dataset["test"],
    shuffle=False,
    batch_size=16,
    collate_fn=data_collator,
)

You're using a RobertaTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


In [ ]:
import tensorflow as tf

model.compile(optimizer=optimizer)

No loss specified in compile() - the model's internal loss computation will be used as the loss. Don't panic - this is a common way to train TensorFlow models in Transformers! To disable this behaviour please pass a loss argument, or explicitly pass `loss=None` if you do not want your model to compute a loss.


In [ ]:
model.fit(x=tf_train_set, validation_data=tf_test_set, epochs=3)

Epoch 1/3
 95/466 [=====>........................] - ETA: 2:28:32 - loss: 8.0116

KeyboardInterrupt: ignored

In [ ]:
prompt = "Somatic hypermutation allows the immune system to"

In [ ]:
from transformers import pipeline

generator = pipeline("text-generation", model="my_awesome_eli5_clm-model")
generator(prompt)

In [ ]:
# pipeline 없다면 - tensorflow 

from transformers import AutoTokenizer
from transformers import TFAutoModelForCausalLM


inputs = tokenizer(prompt, return_tensors="tf").input_ids
outputs = model.generate(input_ids=inputs, max_new_tokens=100, do_sample=True, top_k=50, top_p=0.95)

tokenizer.batch_decode(outputs, skip_special_tokens=True)

## T5

In [ ]:
from transformers import AutoTokenizer, T5ForConditionalGeneration

tokenizer = AutoTokenizer.from_pretrained('hyunwoo3235/t5-v1_1-base-ko', 
                                          bos_token='</s>', eos_token='</s>', unk_token='<unk>')
model = T5ForConditionalGeneration.from_pretrained('hyunwoo3235/t5-v1_1-base-ko')

In [ ]:
config = AutoConfig.from_pretrained('hyunwoo3235/t5-v1_1-base-ko')
config

T5Config {
  "_name_or_path": "hyunwoo3235/t5-v1_1-base-ko",
  "architectures": [
    "T5ForConditionalGeneration"
  ],
  "d_ff": 2048,
  "d_kv": 64,
  "d_model": 768,
  "decoder_start_token_id": 0,
  "dense_act_fn": "gelu_new",
  "dropout_rate": 0.1,
  "eos_token_id": 1,
  "feed_forward_proj": "gated-gelu",
  "initializer_factor": 1.0,
  "is_encoder_decoder": true,
  "is_gated_act": true,
  "layer_norm_epsilon": 1e-06,
  "model_type": "t5",
  "num_decoder_layers": 12,
  "num_heads": 12,
  "num_layers": 12,
  "output_past": true,
  "pad_token_id": 0,
  "relative_attention_max_distance": 128,
  "relative_attention_num_buckets": 32,
  "tie_word_embeddings": false,
  "torch_dtype": "float32",
  "transformers_version": "4.25.1",
  "use_cache": true,
  "vocab_size": 32128
}

In [ ]:
config.update_from_string("vocab_size=32200")

In [ ]:
print(tokenizer.bos_token_id)
print(tokenizer.eos_token_id)
print(tokenizer.pad_token_id)
print('-' * 10)
print(tokenizer.decode(1))
print(tokenizer.decode(2))
print(tokenizer.decode(3))
print(tokenizer.decode(4))

1
1
0
----------
</s>
<unk>
!
"


In [ ]:
tokenizer

PreTrainedTokenizerFast(name_or_path='hyunwoo3235/t5-v1_1-base-ko', vocab_size=32000, model_max_len=1000000000000000019884624838656, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'bos_token': '</s>', 'eos_token': '</s>', 'unk_token': '<unk>', 'pad_token': '<pad>', 'additional_special_tokens': ['<extra_id_0>', '<extra_id_1>', '<extra_id_2>', '<extra_id_3>', '<extra_id_4>', '<extra_id_5>', '<extra_id_6>', '<extra_id_7>', '<extra_id_8>', '<extra_id_9>', '<extra_id_10>', '<extra_id_11>', '<extra_id_12>', '<extra_id_13>', '<extra_id_14>', '<extra_id_15>', '<extra_id_16>', '<extra_id_17>', '<extra_id_18>', '<extra_id_19>', '<extra_id_20>', '<extra_id_21>', '<extra_id_22>', '<extra_id_23>', '<extra_id_24>', '<extra_id_25>', '<extra_id_26>', '<extra_id_27>', '<extra_id_28>', '<extra_id_29>', '<extra_id_30>', '<extra_id_31>', '<extra_id_32>', '<extra_id_33>', '<extra_id_34>', '<extra_id_35>', '<extra_id_36>', '<extra_id_37>', '<extra_id_38>', '<extra_id_39>', '<ex

In [ ]:
tokenizer.all_special_tokens

['</s>',
 '<unk>',
 '<pad>',
 '<extra_id_0>',
 '<extra_id_1>',
 '<extra_id_2>',
 '<extra_id_3>',
 '<extra_id_4>',
 '<extra_id_5>',
 '<extra_id_6>',
 '<extra_id_7>',
 '<extra_id_8>',
 '<extra_id_9>',
 '<extra_id_10>',
 '<extra_id_11>',
 '<extra_id_12>',
 '<extra_id_13>',
 '<extra_id_14>',
 '<extra_id_15>',
 '<extra_id_16>',
 '<extra_id_17>',
 '<extra_id_18>',
 '<extra_id_19>',
 '<extra_id_20>',
 '<extra_id_21>',
 '<extra_id_22>',
 '<extra_id_23>',
 '<extra_id_24>',
 '<extra_id_25>',
 '<extra_id_26>',
 '<extra_id_27>',
 '<extra_id_28>',
 '<extra_id_29>',
 '<extra_id_30>',
 '<extra_id_31>',
 '<extra_id_32>',
 '<extra_id_33>',
 '<extra_id_34>',
 '<extra_id_35>',
 '<extra_id_36>',
 '<extra_id_37>',
 '<extra_id_38>',
 '<extra_id_39>',
 '<extra_id_40>',
 '<extra_id_41>',
 '<extra_id_42>',
 '<extra_id_43>',
 '<extra_id_44>',
 '<extra_id_45>',
 '<extra_id_46>',
 '<extra_id_47>',
 '<extra_id_48>',
 '<extra_id_49>',
 '<extra_id_50>',
 '<extra_id_51>',
 '<extra_id_52>',
 '<extra_id_53>',
 '<extra_

In [ ]:
import pandas as pd
import tqdm
import urllib.request

In [ ]:
train_data = fourth_text
len(train_data)

15604

In [ ]:
def get_chat_data_t5():
  for t in train_data:
    bos_token = [tokenizer.bos_token_id]
    eos_token = [tokenizer.eos_token_id]
    sent = tokenizer.encode(t) 
    yield bos_token + sent + eos_token
     

In [ ]:
dataset = tf.data.Dataset.from_generator(get_chat_data_t5, output_types=tf.int32)

In [ ]:
dataset = dataset.padded_batch(batch_size=batch_size, padded_shapes=(None,), padding_values=tokenizer.pad_token_id)

In [ ]:
for batch in dataset:
    print(batch)
    break     

tf.Tensor(
[[    1  3500   347   364  3734    14   362   788   812   266 10220 31894
    279   544   396    16     1     1     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0]
 [    1   487   801    14  8392   266 15517   340  5787    16     1     1
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0     0     0     0     0
      0     0     0     0     0     0     0     0]
 [    1   464  1642   341  5889 24730  3093   266  8040    16   953 14702
    266   365   216   329   216   252 28911   320    16 14591  2185   256

In [ ]:
tokenizer.decode(batch[0])

'</s>뭐들 하느냐, 그 계집을 얼른 끌어내지 않구.</s></s><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad>'

In [ ]:
tokens, token = [], []

In [ ]:
tokens = []
for i in text:
    for j in i:
        tokens.append(tokenizer.encode(j, return_tensors='pt'))

tokens

[tensor([[252,   1]]),
 tensor([[302,   1]]),
 tensor([[302,   1]]),
 tensor([[382,   1]]),
 tensor([[552,   1]]),
 tensor([[209,   1]]),
 tensor([[765,   1]]),
 tensor([[266,   1]]),
 tensor([[209,   1]]),
 tensor([[794,   1]]),
 tensor([[320,   1]]),
 tensor([[335,   1]]),
 tensor([[284,   1]]),
 tensor([[209,   1]]),
 tensor([[464,   1]]),
 tensor([[442,   1]]),
 tensor([[551,   1]]),
 tensor([[209,   1]]),
 tensor([[316,   1]]),
 tensor([[775,   1]]),
 tensor([[209,   1]]),
 tensor([[302,   1]]),
 tensor([[382,   1]]),
 tensor([[478,   1]]),
 tensor([[209,   1]]),
 tensor([[2028,    1]]),
 tensor([[288,   1]]),
 tensor([[209,   1]]),
 tensor([[498,   1]]),
 tensor([[347,   1]]),
 tensor([[854,   1]]),
 tensor([[209,   1]]),
 tensor([[825,   1]]),
 tensor([[352,   1]]),
 tensor([[299,   1]]),
 tensor([[209,   1]]),
 tensor([[425,   1]]),
 tensor([[928,   1]]),
 tensor([[292,   1]]),
 tensor([[255,   1]]),
 tensor([[16,  1]])]

In [ ]:
adam = tf.keras.optimizers.Adam(learning_rate=3e-5, epsilon=1e-08)

In [ ]:

steps = len(train_data) // batch_size + 1
print(steps)


1951


In [ ]:
import pandas as pd
from tqdm import tqdm
import urllib.request

In [ ]:
import h5py
with open('tf_model.h5', 'r', encoding='utf-8') as f:
    data = f.read()
    

UnicodeDecodeError: ignored

AttributeError: ignored

In [ ]:

group = f[key]

#Checkout what keys are inside that group.
for key in group.keys():
    print(key)

# This assumes group[some_key_inside_the_group] is a dataset, 
# and returns a np.array:
data = group[some_key_inside_the_group][()]
#Do whatever you want with data

#After you are done
f.close()

NameError: ignored

In [ ]:
import numpy as np

In [ ]:
decoded_sentence = tokenizer.decode(output[0].numpy().tolist())

In [ ]:
decoded_sentence

'</s> 오늘도 좋은 하루!</s>'

In [ ]:

def return_answer_by_chatbot(user_text):
  sent = user_text
  input_ids = [tokenizer.bos_token_id] + tokenizer.encode(sent)
  input_ids = tf.convert_to_tensor([input_ids])
  output = model.generate(input_ids, max_length=100, do_sample=True, top_k=20)
  sentence = tokenizer.decode(output[0].numpy().tolist())
  chatbot_response = sentence.replace("</s>", "").strip("<PAD>")
  return chatbot_response

## SKT-GPT2


In [ ]:
!pip install transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 5.8 MB 4.9 MB/s 
     |████████████████████████████████| 7.6 MB 84.4 MB/s 
     |████████████████████████████████| 182 kB 90.5 MB/s 


In [ ]:
import tensorflow as tf
from transformers import AutoTokenizer
from transformers import TFGPT2LMHeadModel

In [ ]:
from transformers import AutoConfig
tokenizer = AutoTokenizer.from_pretrained('skt/kogpt2-base-v2', pad_token = '<PAD>')

config = AutoConfig.from_pretrained('skt/kogpt2-base-v2')
config
# model = TFAutoModel.from_config(config)

Downloading:   0%|          | 0.00/1.00k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.83M [00:00<?, ?B/s]

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


GPT2Config {
  "_name_or_path": "skt/kogpt2-base-v2",
  "_num_labels": 1,
  "activation_function": "gelu_new",
  "architectures": [
    "GPT2LMHeadModel"
  ],
  "attn_pdrop": 0.1,
  "author": "Heewon Jeon(madjakarta@gmail.com)",
  "bos_token_id": 0,
  "created_date": "2021-04-28",
  "embd_pdrop": 0.1,
  "eos_token_id": 1,
  "gradient_checkpointing": false,
  "id2label": {
    "0": "LABEL_0"
  },
  "initializer_range": 0.02,
  "label2id": {
    "LABEL_0": 0
  },
  "layer_norm_epsilon": 1e-05,
  "license": "CC-BY-NC-SA 4.0",
  "model_type": "gpt2",
  "n_ctx": 1024,
  "n_embd": 768,
  "n_head": 12,
  "n_inner": null,
  "n_layer": 12,
  "n_positions": 1024,
  "pad_token_id": 3,
  "reorder_and_upcast_attn": false,
  "resid_pdrop": 0.1,
  "scale_attn_by_inverse_layer_idx": false,
  "scale_attn_weights": true,
  "summary_activation": null,
  "summary_first_dropout": 0.1,
  "summary_proj_to_labels": true,
  "summary_type": "cls_index",
  "summary_use_proj": true,
  "task_specific_params": {
  

In [ ]:
config.update_from_string("vocab_size=52002")

In [ ]:
model = TFGPT2LMHeadModel.from_config(config)

In [ ]:
print(tokenizer.bos_token_id)
print(tokenizer.eos_token_id)
print(tokenizer.pad_token_id)
print('-' * 10)
print(tokenizer.decode(1))
print(tokenizer.decode(2))
print(tokenizer.decode(3))
print(tokenizer.decode(4))

51200
51200
51201
----------
</s>
<usr>
<pad>
<sys>


In [ ]:
tokenizer

PreTrainedTokenizerFast(name_or_path='skt/kogpt2-base-v2', vocab_size=51200, model_max_len=1000000000000000019884624838656, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'bos_token': '<|endoftext|>', 'eos_token': '<|endoftext|>', 'unk_token': '<|endoftext|>', 'pad_token': '<PAD>'})

In [ ]:
tokenizer.all_special_tokens

['<|endoftext|>', '<PAD>']

In [ ]:
import pandas as pd
import tqdm
import urllib.request

In [ ]:
train_data = fourth_text
len(train_data)

15604

In [ ]:
batch_size = 4

In [ ]:
import torch
from transformers import TFGPT2LMHeadModel
model = TFGPT2LMHeadModel.from_pretrained('skt/kogpt2-base-v2', from_pt=True)

Downloading:   0%|          | 0.00/513M [00:00<?, ?B/s]

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFGPT2LMHeadModel: ['transformer.h.2.attn.masked_bias', 'transformer.h.6.attn.masked_bias', 'lm_head.weight', 'transformer.h.8.attn.masked_bias', 'transformer.h.3.attn.masked_bias', 'transformer.h.10.attn.masked_bias', 'transformer.h.0.attn.masked_bias', 'transformer.h.7.attn.masked_bias', 'transformer.h.5.attn.masked_bias', 'transformer.h.11.attn.masked_bias', 'transformer.h.1.attn.masked_bias', 'transformer.h.4.attn.masked_bias', 'transformer.h.9.attn.masked_bias']
- This IS expected if you are initializing TFGPT2LMHeadModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFGPT2LMHeadModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassifica

In [ ]:
from transformers import PreTrainedTokenizerFast
tokenizer = PreTrainedTokenizerFast.from_pretrained(
    "skt/kogpt2-base-v2", bos_token='</s>', eos_token='</s>', 
    unk_token='<unk>', pad_token='<pad>', mask_token='<mask>')

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'GPT2Tokenizer'. 
The class this function is called from is 'PreTrainedTokenizerFast'.


In [ ]:
def get_chat_data():
  for t in train_data:
    bos_token = [tokenizer.bos_token_id]
    eos_token = [tokenizer.eos_token_id]
    sent = tokenizer.encode(t) 
    yield bos_token + sent + eos_token
     

In [ ]:
dataset = tf.data.Dataset.from_generator(get_chat_data, output_types=tf.int32)

In [ ]:
dataset = dataset.padded_batch(batch_size=batch_size, padded_shapes=(None,), padding_values=tokenizer.pad_token_id)

In [ ]:
for batch in dataset:
    print(batch)
    break     

tf.Tensor(
[[    1 46651  7285  9078 13823   387  9022  9142 14401  9903  7469 15130
  28402  9111  6919   389     1     3     3     3     3     3     3     3
      3     3     3     3     3     3     3     3     3     3     3     3
      3     3     3     3     3     3     3     3     3     3     3     3
      3     3     3     3     3     3     3     3     3]
 [    1  9109  7177   387  9095 12615   739  8378  7055   739  7658 12521
      1     3     3     3     3     3     3     3     3     3     3     3
      3     3     3     3     3     3     3     3     3     3     3     3
      3     3     3     3     3     3     3     3     3     3     3     3
      3     3     3     3     3     3     3     3     3]
 [    1  9022 37437 13661 12154  8263  9350 11137 15361  9293 20518  8137
    739  7768  7768  8146  9200  8204 25462 14483 18600  9078 19135   389
   9296  9185 21316  6826  9185   739  7768  7768  8146  9200  8265  9016
  26290  9030 17261  9032  7801  9136  9016  9078 15556 47565

In [ ]:
tokenizer.decode(batch[0])

'</s> 뭐들 하느냐, 그 계집을 얼른 끌어내지 않구.</s><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad>'

In [ ]:
print(tokenizer.encode(' 12시 땡! 하루가 또 가네요.'))

[9349, 7888, 739, 7318, 376, 12557, 6824, 9108, 9028, 7098, 25856]


In [ ]:
tokens, token = [], []

In [ ]:
tokens = []
for i in text:
    for j in i:
        tokens.append(tokenizer.encode(j, return_tensors='pt'))

tokens

[tensor([[9018]]),
 tensor([[9098]]),
 tensor([[9098]]),
 tensor([[9046]]),
 tensor([[9137]]),
 tensor([[739]]),
 tensor([[9031]]),
 tensor([[12014]]),
 tensor([[739]]),
 tensor([[9117]]),
 tensor([[9755]]),
 tensor([[9411]]),
 tensor([[9071]]),
 tensor([[739]]),
 tensor([[9022]]),
 tensor([[9070]]),
 tensor([[9183]]),
 tensor([[739]]),
 tensor([[9039]]),
 tensor([[9300]]),
 tensor([[739]]),
 tensor([[9098]]),
 tensor([[9046]]),
 tensor([[9084]]),
 tensor([[739]]),
 tensor([[9146]]),
 tensor([[9674]]),
 tensor([[739]]),
 tensor([[9129]]),
 tensor([[9625]]),
 tensor([[ 739, 6995]]),
 tensor([[739]]),
 tensor([[9244]]),
 tensor([[9024]]),
 tensor([[36055]]),
 tensor([[739]]),
 tensor([[9535]]),
 tensor([[ 739, 7483]]),
 tensor([[11523]]),
 tensor([[9054]]),
 tensor([[36510]])]

In [ ]:
adam = tf.keras.optimizers.Adam(learning_rate=3e-5, epsilon=1e-08)

In [ ]:
batch_size = 8

In [ ]:

steps = len(train_data) // batch_size + 1
print(steps)


3902


In [ ]:
import pandas as pd
from tqdm import tqdm
import urllib.request

In [ ]:
EPOCHS = 5

for epoch in range(EPOCHS):
  epoch_loss = 0

  for batch in tqdm(dataset, total=steps):
      with tf.GradientTape() as tape:
          result = model(batch, labels=batch)
          loss = result[0]
          batch_loss = tf.reduce_mean(loss)
    #   if batch > steps:
    #       break    
      grads = tape.gradient(batch_loss, model.trainable_variables)
      adam.apply_gradients(zip(grads, model.trainable_variables))
      epoch_loss += batch_loss / steps

      

  print('[Epoch: {:>4}] cost = {:>.9}'.format(epoch + 1, epoch_loss))

100%|█████████▉| 3901/3902 [19:41<00:00,  3.30it/s]


[Epoch:    1] cost = 2.16002679


100%|█████████▉| 3901/3902 [19:21<00:00,  3.36it/s]


[Epoch:    2] cost = 1.70060492


100%|█████████▉| 3901/3902 [19:55<00:00,  3.26it/s]


[Epoch:    3] cost = 1.28998339


100%|█████████▉| 3901/3902 [20:06<00:00,  3.23it/s]


[Epoch:    4] cost = 0.958307624


100%|█████████▉| 3901/3902 [20:08<00:00,  3.23it/s]

[Epoch:    5] cost = 0.723795354


In [ ]:
# token = []

In [ ]:
# for i in tokens:
#     if len(i) < 1025:
#         token.append(i)
# token

[tensor([[9018]]),
 tensor([[9098]]),
 tensor([[9098]]),
 tensor([[9046]]),
 tensor([[9137]]),
 tensor([[739]]),
 tensor([[9031]]),
 tensor([[12014]]),
 tensor([[739]]),
 tensor([[9117]]),
 tensor([[9755]]),
 tensor([[9411]]),
 tensor([[9071]]),
 tensor([[739]]),
 tensor([[9022]]),
 tensor([[9070]]),
 tensor([[9183]]),
 tensor([[739]]),
 tensor([[9039]]),
 tensor([[9300]]),
 tensor([[739]]),
 tensor([[9098]]),
 tensor([[9046]]),
 tensor([[9084]]),
 tensor([[739]]),
 tensor([[9146]]),
 tensor([[9674]]),
 tensor([[739]]),
 tensor([[9129]]),
 tensor([[9625]]),
 tensor([[ 739, 6995]]),
 tensor([[739]]),
 tensor([[9244]]),
 tensor([[9024]]),
 tensor([[36055]]),
 tensor([[739]]),
 tensor([[9535]]),
 tensor([[ 739, 7483]]),
 tensor([[11523]]),
 tensor([[9054]]),
 tensor([[36510]])]

In [ ]:
# len(tokens)

41

In [ ]:
# max_str = token[0]
# for i in range(1, len(token)):
#      if len(max_str) < len(token[i]):
#        max_str = token[i]
# print(len(max_str))

1


In [ ]:
import numpy as np

In [ ]:
# def get_numpy_from_nonfixed_2d_array(aa, fixed_length, padding_value='<pad>'):
#     rows = []
#     for a in aa:
#         rows.append(np.pad(a, (0, fixed_length), 'constant', constant_values=padding_value)[:fixed_length])
#     return np.concatenate(rows, axis=0).reshape(-1, fixed_length)

In [ ]:
#padded_token = get_numpy_from_nonfixed_2d_array(token, fixed_length=42, padding_value=0)

ValueError: ignored

In [ ]:
#  padded_token

NameError: ignored

In [ ]:
# tokens[0]

tensor([[9018]])

In [ ]:
# model.summary()

Model: "tfgpt2lm_head_model_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 transformer (TFGPT2MainLaye  multiple                 125164032 
 r)                                                              
                                                                 
Total params: 125,164,032
Trainable params: 125,164,032
Non-trainable params: 0
_________________________________________________________________


In [ ]:
# optimizer = tf.keras.optimizers.Adam(learning_rate=5e-5)
# loss = tf.keras.losses.SparseCategoricalCrossentropy(from_logits = True)

In [ ]:
# model.compile(optimizer=optimizer, loss=loss, metrics=['accuracy'])

In [ ]:
# model.fit(padded_token, epochs = 1, verbose = 1)

AttributeError: ignored

### Test

In [ ]:
text = '오늘도 좋은 하루!'
sent =  text

In [ ]:
input_ids = [tokenizer.bos_token_id] + tokenizer.encode(sent)
input_ids = tf.convert_to_tensor([input_ids])    

In [ ]:
output = model.generate(input_ids, max_length=50, early_stopping=True, eos_token_id=tokenizer.eos_token_id)
output

<tf.Tensor: shape=(1, 7), dtype=int32, numpy=array([[    1, 10070,  7235, 10586, 12557,   376,     1]], dtype=int32)>

In [ ]:
decoded_sentence = tokenizer.decode(output[0].numpy().tolist())

In [ ]:
decoded_sentence

'</s> 오늘도 좋은 하루!</s>'

In [ ]:
decoded_sentence.replace("</s>", "")

' 오늘도 좋은 하루!'

In [ ]:

def return_answer_by_chatbot(user_text):
  sent = user_text
  input_ids = [tokenizer.bos_token_id] + tokenizer.encode(sent)
  input_ids = tf.convert_to_tensor([input_ids])
  output = model.generate(input_ids, max_length=100, do_sample=True, top_k=20)
  sentence = tokenizer.decode(output[0].numpy().tolist())
  chatbot_response = sentence.replace("</s>", "").strip("<PAD>")
  return chatbot_response

In [ ]:
return_answer_by_chatbot('안녕! 반가워~')


' 안녕! 반가워~ 미친듯이 웃는다. 따라 웃는 제안'

In [ ]:
return_answer_by_chatbot('네놈은 누구냐?')

' 네놈은 누구냐?'

In [ ]:
return_answer_by_chatbot('나랑 영화보자')

' 나랑 영화보자꾸나.'

In [ ]:
return_answer_by_chatbot('이런 망측한 일이 있나')

' 이런 망측한 일이 있나. 안되겠지요. 제안 온다.'

In [ ]:
fourth_text[420]

'마음 편히 하세요. 그래야 그러니까 물으시는 말씀에...'

In [ ]:
return_answer_by_chatbot(fourth_text[420][:5])

' 마음 편히 하세요. 당숙 녹수가 제격일세가 아닙니까. 웃는 제안. 웃지 못하는 송장이 서있다.'

In [ ]:
print(fourth_text[1112])
return_answer_by_chatbot(fourth_text[1112][:-1])

....이리 와요.


'....이리 와요 제안. 뿌리치고 물러서는 박씨 부인. 신씨 부인이 서 있다. 제안, 피하며 천년동안 외치며 살아왔지. 그런데 이만큼 더 살기를 바라느냐. 문득 외치며 외치는 눈물.'

# 실제 구현

## gradio 코드

In [ ]:
import gradio as gr

def image_classifier(inp):
    return {'cat': 0.3, 'dog': 0.7}

demo = gr.Interface(fn=image_classifier, inputs="image", outputs="label")
demo.launch()

## 